## e621.net/e6ai.net JSON to `.txt` tags
----

This Python script is designed to process JSON files found within a specified directory and its subdirectories. Each JSON file is expected to contain data related to image posts, particularly sourced from online platforms such as image boards. The script parses these JSON files, extracts relevant information such as image URL, ratings, and tags, and generates caption files (`.txt`) based on this data.

Here's a breakdown of what the script does:

1. **Ignoring Tags**: The script defines a list of tags to be ignored during processing, such as "hi res", "shaded", etc.

2. **Processing Files**: The `process_file` function is responsible for processing each JSON file. It reads the JSON data, extracts the URL of the image file, determines its rating, and extracts tags associated with the image.

3. **Generating Caption File**: For each image, a caption file is generated with the same name as the image file but with a .txt extension. The rating of the image is written first, followed by processed tags.

4. **Processing Tags**: Tags are processed to replace underscores with spaces and to handle special cases such as artist tags. Ignored tags are filtered out.

In [1]:
# Define tags to be ignored using regular expressions for exact matching
ignored_tags = [r"\bblizzard entertainment\b", r"\bwarcraft\b",
    r"(?:\d{4})|(?:\d+:\d+)",
    r"\bdetailed\b", r"\bwidescreen\b", r"\b4k\b",
    r"\babsurd res\b", r"\bhi res\b", r"\bshaded\b",  r"\bdetailed\b",
    r"\btagme\b",
    r"\bdota\b",
    r"\bcreative commons\b", r"\bcc-by-nc-nd\b",
    r"\bsquare enix\b", r"\bfinal fantasy xiv\b", r"\bfinal fantasy\b",
    r"\bmythological canine\b", r"\basian mythology\b", r"\bmythological scalie\b",
    r"\bancient pokemon\b", r"\bmythological creature\b", r"\blegendary pokemon\b",
    r"\bfelis\b", r"\bfelid\b",
    r"\bsega\b",
    r"\bhasbro\b",
    r"\bzootopia\b",
    r"\bfive nights at freddy's\b",
    r"\beeveelution\b",
    r"\bdisney\b",
    r"\bmammal\b", r"\bcanis\b", r"\bcanine\b", r"\bcanid\b",
    r"\bdigimon\b", r"\bbandai namco\b",
    r"\bpokemon (species)\b",
    r"\bpal (species)\b",
    r"\bpokemon\b", r"\bnintendo\b",
    r"\\bby conditional dnp\\b",
    r"\\bconditional dnp\\b",
    r"\\bconditional_dnp\\b",
    r"\\bby\\s+conditional\\s+dnp\\b",
    r"\bgeneration\s+\d+\s+pokemon\b",
]

In [2]:
import os
import glob
import re
import json
from rich.console import Console
from rich.table import Table

console = Console()


# Function to check if a tag should be ignored based on the ignored_tags list
def should_ignore_tag(tag):
    for ignored_tag_pattern in ignored_tags:
        pattern = re.compile(ignored_tag_pattern, re.VERBOSE | re.IGNORECASE)
        if re.search(pattern, tag):
            return True
    return False


# Function to process tags and determine if they should be ignored
def process_tags(tags_dict):
    processed_tags = []
    for category, tags_list in tags_dict.items():
        category_tags = []
        if category == "artist":
            category_tags = [
                f"by {tag.replace('_', ' ').replace(' (artist)', '')}"
                for tag in tags_list
                if tag
            ]
        else:
            for tag in tags_list:
                tag = tag.replace("_", " ")
                # Escape unescaped parentheses
                tag = re.sub(r"(?<!\\)\(", r"\(", tag)
                tag = re.sub(r"(?<!\\)\)", r"\)", tag)
                if tag.lower() == "artist":
                    continue
                if not should_ignore_tag(tag):
                    category_tags.append(tag)
        processed_tags.extend(category_tags)
    return processed_tags


# Modify the process_file function to use the updated process_tags function
def process_file(file_path):
    try:
        console.print(f"Processing file: [bold]{file_path}[/bold]")
        with open(file_path, "r") as f:
            data = json.load(f)
        # Parse the URL and generate filename
        post_data = data.get("post", {})
        file_data = post_data.get("file", {})
        url = file_data.get("url")
        if url:
            filename, ext = os.path.splitext(os.path.basename(url))
            # Create caption file
            caption_file = f"{filename}.txt"
            caption_path = os.path.join(os.path.dirname(file_path), caption_file)
            with open(caption_path, "w", encoding="utf-8") as f:
                # Write rating
                rating = post_data.get("rating", "q")
                if rating == "s":
                    f.write("rating_safe, ")
                elif rating == "e":
                    f.write("rating_explicit, ")
                else:
                    f.write("rating_questionable, ")
                # Process tags
                tags_data = post_data.get("tags", {})
                processed_tags = process_tags(tags_data)
                # Check if there are any valid tags before writing
                if processed_tags:
                    # Join tags with commas and write to file
                    tags_line = ", ".join(processed_tags)
                    f.write(tags_line.strip())

                    # Create a table
                    table = Table(show_header=True, header_style="bold magenta")
                    table.add_column(caption_path, justify="center")

                    table.add_row(tags_line.strip())

                    # Print the table
                    console.print(table)
    except Exception as e:
        console.print(f"Error processing file: [bold]{file_path}[/bold]")
        console.print(e)


def recursive_process(directory):
    for file_path in glob.glob(directory + "/**/*.json", recursive=True):
        process_file(file_path)


if __name__ == "__main__":
    root_directory = r"E:\training_dir"
    # root_directory = r"C:\Users\kade\Desktop\training_dir_staging"
    recursive_process(root_directory)

Processing file: E:\training_dir\35749.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                              E:\training_dir\cafef2e56850cb1b53f1e340b2ae0791.txt                               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ animal genitalia, animal pussy, anus, backlighting, black claws, black nose, black pawpads, black pussy, butt,  │
│ cheek tuft, claws, day, ears up, facial tuft, female, fence, feral, flower, fluffy, fur, genitals, glistening,  │
│  glistening genitalia, grass, green eyes, grey body, grey fur, inner ear fluff, light, long snout, looking at   │
│   viewer, mouth closed, multicolored body, multicolored fur, outside, pawpads, pink anus, plant, presenting,    │
│ presenting hindquarters, pussy, raised tail, rock, shrub, smile, snout, solo, spread legs, spreading, sunlight, │
│              three-quarter view, tuft, white body, white fur, y anus, blp, wolf, hi res, lighting               │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\35751.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                              E:\training_dir\33d67069c54b96e76baa8133be1bdbc3.txt                               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ animal genitalia, animal pussy, anthro, anus, black body, black claws, black fur, black hair, black nose, black │
│     pussy, breasts, butt, cheek tuft, claws, day, digitigrade, ears back, facial tuft, female, flower, fur,     │
│   genitals, glowing, grass, green eyes, grey body, grey fur, hair, inner ear fluff, light, looking at viewer,   │
│    looking back, looking back at viewer, lying, mouth closed, multicolored body, multicolored fur, on front,    │
│   outside, pawpads, pink anus, pink pawpads, pivoted ears, plant, presenting, presenting hindquarters, pussy,   │
│ raised tail, shrub, side boob, snow, solo, solo focus, spring, sunlight, three-quarter view, tree, tuft, white  │
│                                body, white fur, white hair, y anus, blp, hi res                                 │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\infinite_anal_beads\1169667.json

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                     E:\training_dir\small_dom_big_sub\358ea29b18dbf81d37d00e06b0923be7.txt                      ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   5 fingers, anal, anal penetration, anthro, anthro on anthro, anthro penetrated, anthro penetrating, anthro    │
│   penetrating anthro, anus, balls, big power bottom, biped, bodily fluids, butt, butt grab, claws, dialogue,    │
│   dominant, dominant anthro, dominant male, duo, erection, fingers, genital fluids, genitals, glans, hand on    │
│    butt, heel claw, humanoid genitalia, humanoid penis, larger anthro, larger male, larger penetrated, male,    │
│  male/male, male penetrated, male penetrating, male penetrating male, membrane \(anatomy\), membranous wings,   │
│   muscular, muscular anthro, muscular bottom, muscular dom, muscular male, nude, nude anthro, nude male, open   │
│   mouth, penetration, penile, penile penetration, penis, penis in ass, penis size difference, perineum, pink    │
│  glans, pink penis, plantigrade, power bottom, precum, purple claws, red body, red scales, scales, sex, sharp   │
│  teeth, size difference, small dom big sub, small top big bottom, smaller anthro, smaller male, speech bubble,  │
│   submissive, submissive anthro, submissive male, submissive top, tail, teeth, text, toe claws, white penis,    │
│     wings, by sellon, asian mythology, bakugan, east asian mythology, european mythology, mythology, kenny      │
│ \(drago555\), leonidas \(bakugan\), dragon, eastern dragon, mythological creature, mythological scalie, scalie, │
│                         western dragon, digital media \(artwork\), english text, hi res                         │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\small_dom_big_sub\4101603.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                     E:\training_dir\small_dom_big_sub\be23c2768521f37ed000ec587104e01b.txt                      ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ abs, all fours, anal, anthro, armor, ball size difference, balls, biceps, big balls, big butt, big muscles, big │
│    pecs, big penis, blush, body armor, boots, bottomless, brown body, brown fur, bubble butt, butt, clothed,    │
│ clothing, dialogue, erection, fellatio, footwear, fur, genitals, good boy, grey body, grey fur, group, handjob, │
│    headgear, helmet, huge butt, huge pecs, humanoid genitalia, humanoid penis, male, male/male, mostly nude,    │
│ muscle size difference, muscular, muscular anthro, muscular bottom, muscular legs, muscular male, muscular sub, │
│   nude, oral, outside, pecs, penile, penis, reach around, rimming, rusty trombone, scar, scars all over, sex,   │
│  size difference, small dom big sub, small top big bottom, solo focus, speech bubble, submissive, text, trio,   │
│  two doms one sub, vein, veiny muscles, veiny penis, by zourik, elden ring, fromsoftware, anonymous character,  │
│        blaidd \(elden ring\), dobermann, domestic dog, pinscher, wolf, absurd res, english text, hi res         │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\small_dom_big_sub\637357.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                     E:\training_dir\small_dom_big_sub\898b7653d3684bd1b579a034f081ef97.txt                      ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ anal, animal genitalia, anthro, anthro on feral, anus, balls, bestiality, bodily fluids, bound, candle, chain,  │
│ claws, cuff \(restraint\), digitigrade, duo, erection, feral, foreskin, genital slit, genitals, handjob, horn,  │
│     humanoid genitalia, humanoid penis, looking back, male, male/male, male on feral, male penetrated, male     │
│   penetrating, male penetrating male, membrane \(anatomy\), membranous wings, muscular, nude, oral, outside,    │
│   partially retracted foreskin, penetration, penile, penis, penis tip, plantigrade, reach around, restraints,   │
│       rimming, rusty trombone, saliva, sex, shackles, size difference, small dom big sub, tail, wings, by       │
│     somniferous, mythology, firondraak, dragon, mythological creature, mythological scalie, scalie, hi res      │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

## Delete every JSON file ⚠️

---

In [3]:
import glob
import os

def delete_json_files(directory):
    # Create the path pattern to match JSON files
    pattern = os.path.join(directory, '**', '*.json')
    
    # Find all JSON files using glob
    json_files = glob.glob(pattern, recursive=True)
    
    # Delete each JSON file
    for file_path in json_files:
        try:
            os.remove(file_path)
            print(f"Deleted: {file_path}")
        except OSError as e:
            print(f"Error deleting {file_path}: {e}")

if __name__ == "__main__":
    # Specify the directory path
    directory_path = r'E:\training_dir'
    
    # Call the function to delete JSON files recursively
    delete_json_files(directory_path)

Deleted: E:\training_dir\35749.json
Deleted: E:\training_dir\35751.json
Deleted: E:\training_dir\infinite_anal_beads\1169667.json
Deleted: E:\training_dir\infinite_anal_beads\158177.json
Deleted: E:\training_dir\infinite_anal_beads\2682136.json
Deleted: E:\training_dir\larger_female_smaller_male\1013414.json
Deleted: E:\training_dir\larger_female_smaller_male\1194850.json
Deleted: E:\training_dir\larger_female_smaller_male\1553931.json
Deleted: E:\training_dir\larger_female_smaller_male\1613334.json
Deleted: E:\training_dir\larger_female_smaller_male\1920366.json
Deleted: E:\training_dir\larger_female_smaller_male\2191915.json
Deleted: E:\training_dir\larger_female_smaller_male\2338143.json
Deleted: E:\training_dir\larger_female_smaller_male\2341532.json
Deleted: E:\training_dir\larger_female_smaller_male\2341534.json
Deleted: E:\training_dir\larger_female_smaller_male\2374401.json
Deleted: E:\training_dir\larger_female_smaller_male\2578465.json
Deleted: E:\training_dir\larger_female_s